![ARL](https://miro.medium.com/v2/resize:fit:1400/0*dWxRDPTf891yhxlI.png)

# What is Association Rule Learning

- It is a rule-based machine learning technique used to find patterns in data. The Apriori Algorithm is used while the Association Rule Learning takes place. Apriori is a basket analysis method used to reveal product associations. 

- **There are 3 significant metrics in Apriori:**

- **Support:** Measures how often products X and Y are purchased together
- **Support(X, Y) = Freq(X, Y) / Total Transaction**

- **Confidence:** Probability of purchasing product Y when product X is purchased
- **Confidence(X, Y) = Freq(X, Y) / Freq(X)**

- **Lift:** The coefficient of increase in the probability of purchasing product Y when product X is purchased.
- **Lift = Support(X, Y) / (Support(X) * Support(Y))**

# Business Problem

- Suggesting products to customers at the basket stage.

# Data Story

- The dataset, Online Retail II, contains the sales of a UK-based online retail store between 01/12/2009 and 09/12/2011.
  
 **Variables**

- **InvoiceNo:** Invoice number. The unique number of each transaction, that is, the invoice. Aborted operation if it starts with C.

- **StockCode:** Product code. Unique number for each product.

- **Description:** Product name

- **Quantity:** Number of products. It expresses how many of the products on the invoices have been sold.

- **InvoiceDate:** Invoice date and time.

- **UnitPrice:** Product price (in GBP)

- **CustomerID:** Unique customer number

- **Country:** Country name. Country where the customer lives.

# Road Map

- **1.** Data Preprocessing
- **2.** Preparing the ARL Data Structure (Invoice-Product Matrix)
- **3.** Extraction of Association Rules
- **4.** Preparing the Script of the Study
- **5.** Suggesting Products to Users at the Cart Stage

In [1]:
!pip install mlxtend

In [2]:
# import Required Libraries

import pandas as pd
import numpy as np
from mlxtend.frequent_patterns import apriori, association_rules

In [3]:
# Adjusting Row Column Settings

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.width', 500)
pd.set_option('display.expand_frame_repr', False)

# 1. Data Preprocessing

In [4]:
# Loading the Data Set

df1 = pd.read_excel('/kaggle/input/uci-online-retail-ii-data-set/online_retail_II.xlsx', sheet_name='Year 2009-2010')
df2 = pd.read_excel('/kaggle/input/uci-online-retail-ii-data-set/online_retail_II.xlsx', sheet_name='Year 2010-2011')

In [5]:
# The two data sets were merged.

df_ = pd.concat([df1, df2], ignore_index=True)

In [6]:
df_.head()

Invoice StockCode                          Description  Quantity         InvoiceDate  Price  Customer ID         Country
0  489434     85048  15CM CHRISTMAS GLASS BALL 20 LIGHTS        12 2009-12-01 07:45:00   6.95      13085.0  United Kingdom
1  489434    79323P                   PINK CHERRY LIGHTS        12 2009-12-01 07:45:00   6.75      13085.0  United Kingdom
2  489434    79323W                  WHITE CHERRY LIGHTS        12 2009-12-01 07:45:00   6.75      13085.0  United Kingdom
3  489434     22041         RECORD FRAME 7" SINGLE SIZE         48 2009-12-01 07:45:00   2.10      13085.0  United Kingdom
4  489434     21232       STRAWBERRY CERAMIC TRINKET BOX        24 2009-12-01 07:45:00   1.25      13085.0  United Kingdom

In [7]:
# A copy of the data was made to avoid reloading the data from the beginning.

df = df_.copy()

In [8]:
df.head()

Invoice StockCode                          Description  Quantity         InvoiceDate  Price  Customer ID         Country
0  489434     85048  15CM CHRISTMAS GLASS BALL 20 LIGHTS        12 2009-12-01 07:45:00   6.95      13085.0  United Kingdom
1  489434    79323P                   PINK CHERRY LIGHTS        12 2009-12-01 07:45:00   6.75      13085.0  United Kingdom
2  489434    79323W                  WHITE CHERRY LIGHTS        12 2009-12-01 07:45:00   6.75      13085.0  United Kingdom
3  489434     22041         RECORD FRAME 7" SINGLE SIZE         48 2009-12-01 07:45:00   2.10      13085.0  United Kingdom
4  489434     21232       STRAWBERRY CERAMIC TRINKET BOX        24 2009-12-01 07:45:00   1.25      13085.0  United Kingdom

In [9]:
# Preliminary examination of the data set

def check_df(dataframe, head=5):
    print('##################### Shape #####################')
    print(dataframe.shape)
    print('##################### Types #####################')
    print(dataframe.dtypes)
    print('##################### Head #####################')
    print(dataframe.head(head))
    print('##################### Tail #####################')
    print(dataframe.tail(head))
    print('##################### NA #####################')
    print(dataframe.isnull().sum())
    print('##################### Quantiles #####################')
    print(dataframe.describe([0, 0.05, 0.50, 0.95, 0.99, 1]).T)

check_df(df)

##################### Shape #####################
(1067371, 8)
##################### Types #####################
Invoice                object
StockCode              object
Description            object
Quantity                int64
InvoiceDate    datetime64[ns]
Price                 float64
Customer ID           float64
Country                object
dtype: object
##################### Head #####################
  Invoice StockCode                          Description  Quantity         InvoiceDate  Price  Customer ID         Country
0  489434     85048  15CM CHRISTMAS GLASS BALL 20 LIGHTS        12 2009-12-01 07:45:00   6.95      13085.0  United Kingdom
1  489434    79323P                   PINK CHERRY LIGHTS        12 2009-12-01 07:45:00   6.75      13085.0  United Kingdom
2  489434    79323W                  WHITE CHERRY LIGHTS        12 2009-12-01 07:45:00   6.75      13085.0  United Kingdom
3  489434     22041         RECORD FRAME 7" SINGLE SIZE         48 2009-12-01 07:45:00   2.1

In [10]:
#def retail_data_prep(dataframe):
    #dataframe.dropna(inplace=True)
    #dataframe = dataframe[~dataframe["Invoice"].str.contains("C", na=False)]
    #dataframe = dataframe[dataframe["Quantity"] > 0]
    #dataframe = dataframe[dataframe["Price"] > 0]
    #return dataframe

#df = retail_data_prep(df)

In [11]:
# Outlier threshold setting

def outlier_thresholds(dataframe, variable):
    quartile1 = dataframe[variable].quantile(0.01)
    quartile3 = dataframe[variable].quantile(0.99)
    interquantile_range = quartile3 - quartile1
    up_limit = quartile3 + 1.5 * interquantile_range
    low_limit = quartile1 - 1.5 * interquantile_range
    return low_limit, up_limit

In [12]:
# Replacing outliers with thresholds

def replace_with_thresholds(dataframe, variable):
    low_limit, up_limit = outlier_thresholds(dataframe, variable)
    dataframe.loc[(dataframe[variable] < low_limit), variable] = low_limit
    dataframe.loc[(dataframe[variable] > up_limit), variable] = up_limit

In [13]:
# Pre-processing of the dataset

def retail_data_prep(dataframe):
    dataframe.dropna(inplace=True)
    dataframe = dataframe[~dataframe["Invoice"].str.contains("C", na=False)]
    dataframe = dataframe[dataframe["Quantity"] > 0]
    dataframe = dataframe[dataframe["Price"] > 0]
    replace_with_thresholds(dataframe, "Quantity")
    replace_with_thresholds(dataframe, "Price")
    return dataframe

In [14]:
df = retail_data_prep(df)

In [15]:
df.isnull().sum()

Invoice        0
StockCode      0
Description    0
Quantity       0
InvoiceDate    0
Price          0
Customer ID    0
Country        0
dtype: int64

In [16]:
df.describe().T

count          mean          std        min       25%       50%       75%       max
Quantity     805549.0     11.841087    26.828279      1.000      2.00      5.00     12.00    318.50
Price        805549.0      2.950138     3.238483      0.001      1.25      1.95      3.75     36.94
Customer ID  805549.0  15331.954970  1696.737039  12346.000  13982.00  15271.00  16805.00  18287.00

# 2. Preparing the ARL Data Structure (Invoice-Product Matrix)

In [17]:
# We have chosen a country for the rules of association.

df_fr = df[df['Country'] == "France"]

In [18]:
df_fr.head()

Invoice StockCode                        Description  Quantity         InvoiceDate  Price  Customer ID Country
71  489439     22065     CHRISTMAS PUDDING TRINKET POT       12.0 2009-12-01 09:28:00   1.45      12682.0  France
72  489439     22138      BAKING SET 9 PIECE RETROSPOT        9.0 2009-12-01 09:28:00   4.95      12682.0  France
73  489439     22139  RETRO SPOT TEA SET CERAMIC 11 PC        9.0 2009-12-01 09:28:00   4.95      12682.0  France
74  489439     22352   LUNCHBOX WITH CUTLERY RETROSPOT       12.0 2009-12-01 09:28:00   2.55      12682.0  France
75  489439    85014A   BLACK/BLUE DOTS RUFFLED UMBRELLA       3.0 2009-12-01 09:28:00   5.95      12682.0  France

In [19]:
df_fr.groupby(['Invoice', 'Description']).agg({"Quantity": "sum"}).head(30)

Quantity
Invoice Description                                  
489439   VINTAGE DESIGN GIFT TAGS                12.0
        ASSORTED CAKES FRIDGE MAGNETS            12.0
        ASSORTED COLOUR MINI CASES                2.0
        BAKING SET 9 PIECE RETROSPOT              9.0
        BLACK/BLUE DOTS RUFFLED UMBRELLA          3.0
        CHRISTMAS PUDDING TRINKET POT            12.0
        LUNCHBOX WITH CUTLERY RETROSPOT          12.0
        PACK 20 DOLLY PEGS                       12.0
        PARTY CONE CHRISTMAS DECORATION          24.0
        PINK DOUGHNUT TRINKET POT                12.0
        POSTAGE                                   3.0
        RED TOADSTOOL LED NIGHT LIGHT            24.0
        RED/WHITE DOTS RUFFLED UMBRELLA           3.0
        RETRO SPORT PARTY BAG + STICKER SET       8.0
        RETRO SPOT TEA SET CERAMIC 11 PC          9.0
        SET OF THREE VINTAGE GIFT WRAPS           6.0
        SET/3 RUSSIAN DOLL STACKING TINS          6.0
        WRAP BLUE RUSSIAN FOLKART                25.0
        WRAP ENGLISH ROSE                        25.0
489557  BASKET OF TOADSTOOLS                     12.0
        JUMBO BAG RED WHITE SPOTTY               20.0
        JUMBO BAG TOYS                           10.0
        JUMBO BAG WOODLAND ANIMALS               10.0
        LUNCHBOX WITH CUTLERY FAIRY CAKES         6.0
        LUNCHBOX WITH CUTLERY RETROSPOT          12.0
        PACK OF 72 RETRO SPOT CAKE CASES         24.0
        POSTAGE                                   4.0
        RED BIRD HOUSE TREE DECORATION          192.0
        RED SPOTTY CHILDS UMBRELLA                6.0
        RED SPOTTY COIR DOORMAT                   2.0

In [20]:
df_fr.groupby(['Invoice', 'Description']).agg({"Quantity": "sum"}).unstack().iloc[0:5, 0:5]

Quantity                                                                                       
Description  50'S CHRISTMAS GIFT BAG LARGE  DOLLY GIRL BEAKER  FLAMINGO LIGHTS  I LOVE LONDON MINI BACKPACK  LARGE SKULL WINDMILL
Invoice                                                                                                                          
489439                                 NaN                NaN              NaN                          NaN                   NaN
489557                                 NaN                NaN              NaN                          NaN                   NaN
489883                                 NaN                NaN              NaN                          NaN                   NaN
490139                                 NaN                NaN              NaN                          NaN                   NaN
490152                                 NaN                NaN              NaN                          NaN                   NaN

In [21]:
df_fr.groupby(['Invoice', 'Description']).agg({"Quantity": "sum"}).unstack().fillna(0).iloc[0:5, 0:5]

Quantity                                                                                       
Description  50'S CHRISTMAS GIFT BAG LARGE  DOLLY GIRL BEAKER  FLAMINGO LIGHTS  I LOVE LONDON MINI BACKPACK  LARGE SKULL WINDMILL
Invoice                                                                                                                          
489439                                 0.0                0.0              0.0                          0.0                   0.0
489557                                 0.0                0.0              0.0                          0.0                   0.0
489883                                 0.0                0.0              0.0                          0.0                   0.0
490139                                 0.0                0.0              0.0                          0.0                   0.0
490152                                 0.0                0.0              0.0                          0.0                   0.0

In [22]:
# Setting data to 1 and 0. using Description 

df_fr.groupby(['Invoice', 'Description']). \
    agg({"Quantity": "sum"}). \
    unstack(). \
    fillna(0). \
    applymap(lambda x: 1 if x > 0 else 0).iloc[0:5, 0:5]

Quantity                                                                                       
Description  50'S CHRISTMAS GIFT BAG LARGE  DOLLY GIRL BEAKER  FLAMINGO LIGHTS  I LOVE LONDON MINI BACKPACK  LARGE SKULL WINDMILL
Invoice                                                                                                                          
489439                                   0                  0                0                            0                     0
489557                                   0                  0                0                            0                     0
489883                                   0                  0                0                            0                     0
490139                                   0                  0                0                            0                     0
490152                                   0                  0                0                            0                     0

In [23]:
# Setting data to 1 and 0. using StockCode 

df_fr.groupby(['Invoice', 'StockCode']).agg({"Quantity": "sum"}).unstack().fillna(0).applymap(lambda x: 1 if x > 0 else 0).iloc[0:5, 0:5]

Quantity                        
StockCode    10002 10120 10125 10135 11001
Invoice                                   
489439           0     0     0     0     0
489557           0     0     0     0     0
489883           0     0     0     0     0
490139           0     0     0     0     0
490152           0     0     0     0     0

In [24]:
# using program

def create_invoice_product_df(dataframe, id=False):
    if id:
        return dataframe.groupby(['Invoice', "StockCode"])['Quantity'].sum().unstack().fillna(0).applymap(lambda x: 1 if x > 0 else 0)
    else:
        return dataframe.groupby(['Invoice', 'Description'])['Quantity'].sum().unstack().fillna(0).applymap(lambda x: 1 if x > 0 else 0)

In [25]:
fr_inv_pro_df = create_invoice_product_df(df_fr)

In [26]:
fr_inv_pro_df.head(20)

Description   50'S CHRISTMAS GIFT BAG LARGE   DOLLY GIRL BEAKER   FLAMINGO LIGHTS   I LOVE LONDON MINI BACKPACK   LARGE SKULL WINDMILL   NINE DRAWER OFFICE TIDY   RED/WHITE DOT MINI CASES   SET 2 TEA TOWELS I LOVE LONDON    SPACEBOY BABY GIFT SET   TRELLIS COAT RACK   VINTAGE DESIGN GIFT TAGS  10 COLOUR SPACEBOY PEN  12 COLOURED PARTY BALLOONS  12 EGG HOUSE PAINTED WOOD  12 IVORY ROSE PEG PLACE SETTINGS  12 MESSAGE CARDS WITH ENVELOPES  12 PENCIL SMALL TUBE WOODLAND  12 PENCILS SMALL TUBE POSY  12 PENCILS SMALL TUBE RED RETROSPOT  12 PENCILS SMALL TUBE RED SPOTTY  12 PENCILS SMALL TUBE SKULL  12 PENCILS TALL TUBE POSY  12 PENCILS TALL TUBE RED RETROSPOT  12 PENCILS TALL TUBE RED SPOTTY  12 PENCILS TALL TUBE SKULLS  12 PENCILS TALL TUBE WOODLAND  12 RED ROSE PEG PLACE SETTINGS  15CM CHRISTMAS GLASS BALL 20 LIGHTS  16 PIECE CUTLERY SET PANTRY DESIGN  18PC WOODEN CUTLERY SET DISPOSABLE  2 DAISIES HAIR COMB  20 DOLLY PEGS RETROSPOT  200 RED + WHITE BENDY STRAWS  3 HEARTS HANGING DECORATION RUSTIC  3 HOOK HANGER MAGIC GARDEN  3 PIECE SPACEBOY COOKIE CUTTER SET  3 RAFFIA RIBBONS 50'S CHRISTMAS   3 STRIPEY MICE FELTCRAFT  3 TIER CAKE TIN RED AND CREAM  3 TRADITIONAl BISCUIT CUTTERS  SET  36 DOILIES DOLLY GIRL  36 DOILIES VINTAGE CHRISTMAS  36 FOIL HEART CAKE CASES  36 FOIL STAR CAKE CASES   36 PENCILS TUBE RED RETROSPOT  36 PENCILS TUBE RED SPOTTY  36 PENCILS TUBE SKULLS  36 PENCILS TUBE WOODLAND  3D HEARTS  HONEYCOMB PAPER GARLAND  3D SHEET OF CAT STICKERS  3D SHEET OF DOG STICKERS  3D TRADITIONAL CHRISTMAS STICKERS  3D VINTAGE CHRISTMAS STICKERS   4 IVORY DINNER CANDLES GOLD FLOCK  4 IVORY DINNER CANDLES SILVER FLOCK  4 PINK DINNER CANDLE SILVER FLOCK  4 PINK FLOCK CHRISTMAS BALLS  4 TRADITIONAL SPINNING TOPS  5 HOOK HANGER MAGIC TOADSTOOL  5 HOOK HANGER RED MAGIC TOADSTOOL  50CM METAL STRING WITH  7 CLIPS  6 CHOCOLATE LOVE HEART T-LIGHTS  6 CROCHET STRAWBERRIES  6 GIFT TAGS 50'S CHRISTMAS   6 GIFT TAGS VINTAGE CHRISTMAS   6 RIBBONS ELEGANT CHRISTMAS   6 RIBBONS EMPIRE    6 RIBBONS RUSTIC CHARM  6 ROCKET BALLOONS   60 CAKE CASES DOLLY GIRL DESIGN  60 CAKE CASES VINTAGE CHRISTMAS  60 TEATIME FAIRY CAKE CASES  6PC WOOD PLATE SET DISPOSABLE  72 ROUND PINK DOILIES  72 SWEETHEART FAIRY CAKE CASES  75 GREEN FAIRY CAKE CASES  75 GREEN PETIT FOUR CASES  A PRETTY THANK YOU CARD  ABC TREASURE BOOK BOX   ABSTRACT CIRCLES SKETCHBOOK   ADULT APRON APPLE DELIGHT  ADVENT CALENDAR GINGHAM SACK  AGED GLASS SILVER T-LIGHT HOLDER  AIRLINE BAG VINTAGE JET SET BROWN  AIRLINE BAG VINTAGE JET SET RED  AIRLINE BAG VINTAGE JET SET WHITE  AIRLINE BAG VINTAGE TOKYO 78  AIRLINE BAG VINTAGE WORLD CHAMPION   AIRLINE LOUNGE,METAL SIGN  ALARM CLOCK BAKELIKE CHOCOLATE  ALARM CLOCK BAKELIKE GREEN  ALARM CLOCK BAKELIKE IVORY  ALARM CLOCK BAKELIKE ORANGE  ALARM CLOCK BAKELIKE PINK  ALARM CLOCK BAKELIKE RED   ALPHABET HEARTS STICKER SHEET  ALUMINIUM STAMPED HEART  AMETHYST CHUNKY BEAD BRACELET W STR  ANGEL DECORATION STARS ON DRESS  ANTIQUE ALL GLASS CANDLESTICK  ANTIQUE GLASS DRESSING TABLE POT  ANTIQUE GLASS HEART DECORATION   ANTIQUE GLASS PEDESTAL BOWL  ANTIQUE GLASS RIDGED HANGING BALL  ANTIQUE LILY FAIRY LIGHTS  ANTIQUE SILVER BAUBLE LAMP    ANTIQUE SILVER T-LIGHT GLASS  ANTIQUE SILVER TEA GLASS ENGRAVED  APPLE BATH SPONGE  AREA PATROLLED METAL SIGN  ARMY CAMO WRAPPING TAPE  ASS COLOUR GLOWING TIARAS  ASS FLORAL PRINT MULTI SCREWDRIVER  ASS FLORAL PRINT SCISSORS  ASSORTED BOTTLE TOP  MAGNETS   ASSORTED CAKES FRIDGE MAGNETS  ASSORTED COLOUR BIRD ORNAMENT  ASSORTED COLOUR MINI CASES  ASSORTED COLOUR SILK COIN PURSE  ASSORTED COLOUR SILK COSMETIC PURSE  ASSORTED COLOUR T-LIGHT HOLDER  ASSORTED COLOURS SILK FAN  ASSORTED EASTER DECORATIONS  BELLS  ASSORTED EASTER GIFT TAGS  ASSORTED FLOWER COLOUR "LEIS"  ASSORTED ICE CREAM FRIDGE MAGNETS  ASSORTED INCENSE PACK  ASSORTED TUTTI FRUTTI BRACELET  ASSORTED TUTTI FRUTTI HEART BOX  ASSORTED TUTTI FRUTTI MIRROR  ASSORTED TUTTI FRUTTI SMALL PURSE  ASSTD DESIGN 3D PAPER STICKERS  ASSTD DESIGN BUBBLE GUM RING  ASSTD DESIGN POP

In [27]:
# according to id number 
fr_inv_pro_df_id = create_invoice_product_df(df_fr, id=True)

In [28]:
fr_inv_pro_df_id.head(20)

StockCode  10002  10120  10125  10135  11001  15036  15039  16012  16043  16046  16047  16048  16053  16218  16219  16225  16235  16236  16237  16238  16259  17003  17174  17181  20615  20617  20619  20622  20652  20658  20661  20662  20663  20665  20666  20668  20669  20670  20674  20675  20676  20677  20679  20681  20682  20684  20685  20686  20696  20700  20702  20703  20704  20711  20712  20713  20716  20717  20718  20719  20723  20724  20725  20726  20727  20728  20734  20749  20750  20751  20752  20754  20764  20767  20769  20771  20777  20795  20819  20832  20865  20866  20867  20886  20893  20897  20898  20914  20932  20940  20941  20943  20960  20961  20963  20966  20967  20970  20971  20972  20973  20974  20975  20976  20977  20978  20979  20981  20982  20983  20984  20992  20996  20997  21010  21012  21017  21026  21027  21030  21034  21035  21039  21040  21041  21042  21054  21055  21056  21058  21059  21061  21062  21063  21064  21065  21068  21069  21070  21071  21076  21077  21078  21080  21082  21084  21085  21086  21087  21088  21089  21090  21091  21092  21094  21095  21096  21098  21099  21100  21108  21109  21110  21111  21114  21115  21116  21121  21122  21123  21124  21125  21126  21130  21135  21136  21137  21143  21144  21146  21153  21154  21155  21156  21157  21158  21161  21162  21163  21164  21165  21166  21169  21172  21174  21175  21181  21186  21188  21189  21190  21194  21195  21196  21197  21198  21199  21200  21201  21202  21203  21204  21205  21206  21207  21208  21209  21210  21211  21212  21213  21214  21215  21216  21217  21218  21219  21220  21221  21222  21223  21224  21226  21231  21232  21238  21239  21240  21241  21242  21243  21244  21245  21246  21247  21248  21249  21251  21255  21257  21258  21259  21260  21262  21265  21278  21279  21280  21281  21284  21286  21293  21294  21306  21314  21326  21327  21328  21329  21330  21333  21336  21340  21341  21351  21354  21355  21356  21357  21358  21361  21365  21369  21371  21372  21374  21375  21377  21380  21381  21383  21385  21392  21393  21394  21395  21396  21397  21398  21399  21401  21402  21403  21407  21408  21410  21411  21424  21425  21426  21427  21428  21429  21430  21431  21432  21439  21441  21442  21446  21447  21452  21463  21464  21466  21467  21469  21470  21471  21472  21479  21481  21484  21485  21488  21491  21493  21494  21495  21497  21498  21499  21500  21504  21506  21507  21508  21509  21519  21523  21524  21527  21528  21529  21531  21533  21535  21537  21539  21541  21542  21544  21555  21556  21557  21558  21559  21561  21562  21563  21564  21576  21577  21578  21579  21580  21581  21584  21586  21588  21591  21592  21613  21614  21621  21622  21623  21624  21625  21627  21628  21632  21633  21643  21644  21648  21650  21653  21655  21656  21658  21668  21669  21670  21671  21672  21673  21675  21677  21678  21679  21680  21689  21693  21696  21697  21698  21700  21703  21704  21706  21707  21708  21709  21710  21711  21715  21716  21717  21718  21719  21720  21721  21722  21723  21724  21725  21726  21731  21733  21739  21741  21746  21747  21749  21750  21754  21755  21756  21765  21770  21774  21786  21787  21788  21789  21790  21791  21802  21806  21812  21813  21818  21819  21821  21826  21827  21828  21829  21832  21833  21841  21843  21844  21845  21864  21865  21866  21868  21870  21871  21872  21875  21877  21879  21880  21881  21882  21883  21884  21888  21889  21890  21891  21892  21894  21899  21900  21901  21902  21905  21906  21907  21908  21912  21913  21914  21915  21916  21917  21918  21922  21926  21928  21929  21930  21931  21932  21933  21934  21935  21936  21937  21943  21945  21946  21947  21948  21949  21955  21967  21972  21973  21974  21975  21976  21977  21980  21981  21982  21983  21984  21985  21986  21987  21988  21989  21990  21993  22021  22023  22024  22025  22026  22027  22028  22029  22030  22032  22034  22035  22036  22037  22041  22042  22043  22044  22045  22046  22051 

In [29]:
# check stock_code

def check_id(dataframe, stock_code):
    product_name = dataframe[dataframe["StockCode"] == stock_code][["Description"]].values[0].tolist()
    print(product_name)

In [30]:
check_id(df_fr, 10120)

['DOGGY RUBBER']


In [31]:
check_id(df_fr, 10002)

['INFLATABLE POLITICAL GLOBE ']


In [32]:
check_id(df_fr, 16043)

['POP ART PUSH DOWN RUBBER ']


In [33]:
check_id(df_fr, 20615)

['BLUE SPOTTY PASSPORT COVER']


# 3. Extraction of Association Rules

- This will be to find the support values, that is, the probabilities, of all possible product associations. 


In [34]:
frequent_itemsets = apriori(fr_inv_pro_df,
                            min_support=0.01,
                            use_colnames=True)

/opt/conda/lib/python3.10/site-packages/mlxtend/frequent_patterns/fpcommon.py:110: DeprecationWarning: DataFrames with non-bool types result in worse computationalperformance and their support might be discontinued in the future.Please use a DataFrame with bool type
  warnings.warn(


In [35]:
frequent_itemsets.sort_values("support", ascending=False).head(20)

support                                        itemsets
305   0.758958                                       (POSTAGE)
353   0.210098                 (RED TOADSTOOL LED NIGHT LIGHT)
2411  0.187296        (RED TOADSTOOL LED NIGHT LIGHT, POSTAGE)
380   0.175896           (ROUND SNACK BOXES SET OF4 WOODLAND )
293   0.169381                (PLASTERS IN TIN CIRCUS PARADE )
2428  0.159609  (ROUND SNACK BOXES SET OF4 WOODLAND , POSTAGE)
298   0.157980              (PLASTERS IN TIN WOODLAND ANIMALS)
213   0.153094             (LUNCH BOX WITH CUTLERY RETROSPOT )
444   0.138436                   (SET/6 RED SPOTTY PAPER CUPS)
2199  0.138436       (PLASTERS IN TIN CIRCUS PARADE , POSTAGE)
2312  0.131922     (PLASTERS IN TIN WOODLAND ANIMALS, POSTAGE)
472   0.130293             (STRAWBERRY LUNCH BOX WITH CUTLERY)
464   0.130293                           (SPACEBOY LUNCH BOX )
295   0.128664                      (PLASTERS IN TIN SPACEBOY)
445   0.127036                 (SET/6 RED SPOTTY PAPER PLATES)
1839  0.125407    (LUNCH BOX WITH CUTLERY RETROSPOT , POSTAGE)
378   0.125407            (ROUND SNACK BOXES SET OF 4 FRUITS )
210   0.118893                            (LUNCH BAG WOODLAND)
307   0.118893                            (RABBIT NIGHT LIGHT)
2474  0.117264          (SET/6 RED SPOTTY PAPER CUPS, POSTAGE)

In [36]:
rules = association_rules(frequent_itemsets,
                          metric="support",
                          min_threshold=0.01)

- **antecedents:** first product
- **consequents:** second product
- **antecedent support:** the probability of observing the first product alone
- **consequent support:** the probability of observing the second product alone
- **support:** Probability of 1st and 2nd product being observed together
- **confidence:** The probability of purchasing product Y when product X is purchased.
- **lift:** It shows how many times product Y will increase when product X is purchased.
- **leverage:** similar to lift but it gives priority to higher support.
- **conviction:** expected frequency of antecedents X without consequent Y
- **zhangs_metric:**

In [37]:
rules[(rules["support"]>0.05) & (rules["confidence"]>0.1) & (rules["lift"]>5)]

antecedents                                        consequents  antecedent support  consequent support   support  confidence       lift  leverage  conviction  zhangs_metric
154                          (ALARM CLOCK BAKELIKE PINK)                       (ALARM CLOCK BAKELIKE GREEN)            0.073290            0.068404  0.053746    0.733333  10.720635  0.048733    3.493485       0.978431
155                         (ALARM CLOCK BAKELIKE GREEN)                        (ALARM CLOCK BAKELIKE PINK)            0.068404            0.073290  0.053746    0.785714  10.720635  0.048733    4.324647       0.973299
156                          (ALARM CLOCK BAKELIKE RED )                       (ALARM CLOCK BAKELIKE GREEN)            0.068404            0.068404  0.057003    0.833333  12.182540  0.052324    5.589577       0.985315
157                         (ALARM CLOCK BAKELIKE GREEN)                        (ALARM CLOCK BAKELIKE RED )            0.068404            0.068404  0.057003    0.833333  12.182540  0.052324    5.589577       0.985315
260                          (ALARM CLOCK BAKELIKE PINK)                        (ALARM CLOCK BAKELIKE RED )            0.073290            0.068404  0.055375    0.755556  11.045503  0.050361    3.811075       0.981392
261                          (ALARM CLOCK BAKELIKE RED )                        (ALARM CLOCK BAKELIKE PINK)            0.068404            0.073290  0.055375    0.809524  11.045503  0.050361    4.865228       0.976244
1324                          (CIRCUS PARADE LUNCH BOX )                              (SPACEBOY LUNCH BOX )            0.087948            0.130293  0.060261    0.685185   5.258796  0.048802    2.762598       0.887934
1325                               (SPACEBOY LUNCH BOX )                         (CIRCUS PARADE LUNCH BOX )            0.130293            0.087948  0.060261    0.462500   5.258796  0.048802    1.696841       0.931167
1544                               (SPACEBOY LUNCH BOX )                             (DOLLY GIRL LUNCH BOX)            0.130293            0.096091  0.073290    0.562500   5.853814  0.060770    2.066077       0.953392
1545                              (DOLLY GIRL LUNCH BOX)                              (SPACEBOY LUNCH BOX )            0.096091            0.130293  0.073290    0.762712   5.853814  0.060770    3.665193       0.917317
4576               (SET/20 RED RETROSPOT PAPER NAPKINS )                      (SET/6 RED SPOTTY PAPER CUPS)            0.096091            0.138436  0.073290    0.762712   5.509472  0.059987    3.630875       0.905506
4577                       (SET/6 RED SPOTTY PAPER CUPS)              (SET/20 RED RETROSPOT PAPER NAPKINS )            0.138436            0.096091  0.073290    0.529412   5.509472  0.059987    1.920806       0.950011
4578               (SET/20 RED RETROSPOT PAPER NAPKINS )                    (SET/6 RED SPOTTY PAPER PLATES)            0.096091            0.127036  0.073290    0.762712   6.003911  0.061083    3.678920       0.922042
4579                     (SET/6 RED SPOTTY PAPER PLATES)              (SET/20 RED RETROSPOT PAPER NAPKINS )            0.127036            0.096091  0.073290    0.576923   6.003911  0.061083    2.136512       0.954726
4594                       (SET/6 RED SPOTTY PAPER CUPS)                    (SET/6 RED SPOTTY PAPER PLATES)            0.138436            0.127036  0.115635    0.835294   6.575264  0.098049    5.300140       0.984158
4595                     (SET/6 RED SPOTTY PAPER PLATES)                      (SET/6 RED SPOTTY PAPER CUPS)            0.127036            0.138436  0.115635    0.910256   6.575264  0.098049    9.600279       0.971305
5354                (ALARM CLOCK BAKELIKE RED , POSTAGE)                       (ALARM CLOCK BAKELIKE GREEN)            0.061889            0.068404  0.050489    0.815789  11.926065  0.046255    5.057236       0.976591
5356               (POSTAGE, ALARM CLOCK BAKELIKE GREEN)                        (ALARM CLOCK BAKELIKE RED )            0.

In [38]:
check_id(df_fr, 21086)

['SET/6 RED SPOTTY PAPER CUPS']


In [39]:
rules[(rules["support"]>0.05) & (rules["confidence"]>0.1) & (rules["lift"]>5)]. \
sort_values("confidence", ascending=False)

antecedents                                        consequents  antecedent support  consequent support   support  confidence       lift  leverage  conviction  zhangs_metric
22383  (SET/20 RED RETROSPOT PAPER NAPKINS , SET/6 RE...                      (SET/6 RED SPOTTY PAPER CUPS)            0.073290            0.138436  0.071661    0.977778   7.063007  0.061515   38.770358       0.926306
22382  (SET/20 RED RETROSPOT PAPER NAPKINS , SET/6 RE...                    (SET/6 RED SPOTTY PAPER PLATES)            0.073290            0.127036  0.071661    0.977778   7.696866  0.062351   39.283388       0.938888
46218  (SET/20 RED RETROSPOT PAPER NAPKINS , SET/6 RE...                      (SET/6 RED SPOTTY PAPER CUPS)            0.060261            0.138436  0.058632    0.972973   7.028299  0.050290   31.877850       0.912719
46217  (SET/20 RED RETROSPOT PAPER NAPKINS , SET/6 RE...                    (SET/6 RED SPOTTY PAPER PLATES)            0.060261            0.127036  0.058632    0.972973   7.659044  0.050977   32.299674       0.925188
4595                     (SET/6 RED SPOTTY PAPER PLATES)                      (SET/6 RED SPOTTY PAPER CUPS)            0.127036            0.138436  0.115635    0.910256   6.575264  0.098049    9.600279       0.971305
21664           (SET/6 RED SPOTTY PAPER PLATES, POSTAGE)                      (SET/6 RED SPOTTY PAPER CUPS)            0.107492            0.138436  0.096091    0.893939   6.457398  0.081210    8.123313       0.946926
5356               (POSTAGE, ALARM CLOCK BAKELIKE GREEN)                        (ALARM CLOCK BAKELIKE RED )            0.058632            0.068404  0.050489    0.861111  12.588624  0.046478    6.707492       0.977899
4594                       (SET/6 RED SPOTTY PAPER CUPS)                    (SET/6 RED SPOTTY PAPER PLATES)            0.138436            0.127036  0.115635    0.835294   6.575264  0.098049    5.300140       0.984158
156                          (ALARM CLOCK BAKELIKE RED )                       (ALARM CLOCK BAKELIKE GREEN)            0.068404            0.068404  0.057003    0.833333  12.182540  0.052324    5.589577       0.985315
157                         (ALARM CLOCK BAKELIKE GREEN)                        (ALARM CLOCK BAKELIKE RED )            0.068404            0.068404  0.057003    0.833333  12.182540  0.052324    5.589577       0.985315
21663             (SET/6 RED SPOTTY PAPER CUPS, POSTAGE)                    (SET/6 RED SPOTTY PAPER PLATES)            0.117264            0.127036  0.096091    0.819444   6.450499  0.081194    4.834878       0.957221
5354                (ALARM CLOCK BAKELIKE RED , POSTAGE)                       (ALARM CLOCK BAKELIKE GREEN)            0.061889            0.068404  0.050489    0.815789  11.926065  0.046255    5.057236       0.976591
261                          (ALARM CLOCK BAKELIKE RED )                        (ALARM CLOCK BAKELIKE PINK)            0.068404            0.073290  0.055375    0.809524  11.045503  0.050361    4.865228       0.976244
42495  (PLASTERS IN TIN CIRCUS PARADE , POSTAGE, PLAS...                 (PLASTERS IN TIN WOODLAND ANIMALS)            0.068404            0.157980  0.055375    0.809524   5.124202  0.044568    4.420603       0.863945
46220  (SET/20 RED RETROSPOT PAPER NAPKINS , SET/6 RE...           (SET/6 RED SPOTTY PAPER PLATES, POSTAGE)            0.073290            0.107492  0.058632    0.800000   7.442424  0.050754    4.462541       0.934095
46221  (SET/20 RED RETROSPOT PAPER NAPKINS , SET/6 RE...             (SET/6 RED SPOTTY PAPER CUPS, POSTAGE)            0.073290            0.117264  0.058632    0.800000   6.822222  0.050038    4.413681       0.920914
155                         (ALARM CLOCK BAKELIKE GREEN)                        (ALARM CLOCK BAKELIKE PINK)            0.068404            0.073290  0.053746    0.785714  10.720635  0.048733    4.324647       0.973299
4578               (SET/20 RED RETROSPOT PAPER NAPKINS )                    (SET/6 RED SPOTTY PAPER PLATES)            0.

# 4. Preparing the Script of the Study

In [40]:
def outlier_thresholds(dataframe, variable):
    quartile1 = dataframe[variable].quantile(0.01)
    quartile3 = dataframe[variable].quantile(0.99)
    interquantile_range = quartile3 - quartile1
    up_limit = quartile3 + 1.5 * interquantile_range
    low_limit = quartile1 - 1.5 * interquantile_range
    return low_limit, up_limit

In [41]:
def replace_with_thresholds(dataframe, variable):
    low_limit, up_limit = outlier_thresholds(dataframe, variable)
    dataframe.loc[(dataframe[variable] < low_limit), variable] = low_limit
    dataframe.loc[(dataframe[variable] > up_limit), variable] = up_limit

In [42]:
def retail_data_prep(dataframe):
    dataframe.dropna(inplace=True)
    dataframe = dataframe[~dataframe["Invoice"].str.contains("C", na=False)]
    dataframe = dataframe[dataframe["Quantity"] > 0]
    dataframe = dataframe[dataframe["Price"] > 0]
    replace_with_thresholds(dataframe, "Quantity")
    replace_with_thresholds(dataframe, "Price")
    return dataframe

In [43]:
def create_invoice_product_df(dataframe, id=False):
    if id:
        return dataframe.groupby(['Invoice', "StockCode"])['Quantity'].sum().unstack().fillna(0).applymap(lambda x: 1 if x > 0 else 0)
    else:
        return dataframe.groupby(['Invoice', 'Description'])['Quantity'].sum().unstack().fillna(0).applymap(lambda x: 1 if x > 0 else 0)

In [44]:
def check_id(dataframe, stock_code):
    product_name = dataframe[dataframe["StockCode"] == stock_code][["Description"]].values[0].tolist()
    print(product_name)

In [45]:
def create_rules(dataframe, id=True, country="France"):
    dataframe = dataframe[dataframe['Country'] == country]
    dataframe = create_invoice_product_df(dataframe, id)
    frequent_itemsets = apriori(dataframe, min_support=0.01, use_colnames=True)
    rules = association_rules(frequent_itemsets, metric="support", min_threshold=0.01)
    return rules

In [46]:
df = df_.copy()

In [47]:
df = retail_data_prep(df)

In [48]:
rules = create_rules(df)

/opt/conda/lib/python3.10/site-packages/mlxtend/frequent_patterns/fpcommon.py:110: DeprecationWarning: DataFrames with non-bool types result in worse computationalperformance and their support might be discontinued in the future.Please use a DataFrame with bool type
  warnings.warn(


In [49]:
rules[(rules["support"]>0.05) & (rules["confidence"]>0.1) & (rules["lift"]>5)]. \
sort_values("confidence", ascending=False)

antecedents           consequents  antecedent support  consequent support   support  confidence       lift  leverage  conviction  zhangs_metric
47334  (21080, POST, 21086)               (21094)            0.078176            0.127036  0.074919    0.958333   7.543803  0.064987   20.951140       0.941005
14591        (21080, 21094)               (21086)            0.096091            0.138436  0.091205    0.949153   6.856231  0.077903   16.944083       0.944949
14590        (21080, 21086)               (21094)            0.096091            0.127036  0.091205    0.949153   7.471534  0.078998   17.168295       0.958237
47336  (21080, POST, 21094)               (21086)            0.079805            0.138436  0.074919    0.938776   6.781273  0.063871   14.072204       0.926472
1585                (21094)               (21086)            0.127036            0.138436  0.115635    0.910256   6.575264  0.098049    9.600279       0.971305
15930         (POST, 21094)               (21086)            0.107492            0.138436  0.096091    0.893939   6.457398  0.081210    8.123313       0.946926
31042         (POST, 22726)               (22727)            0.058632            0.068404  0.050489    0.861111  12.588624  0.046478    6.707492       0.977899
1584                (21086)               (21094)            0.138436            0.127036  0.115635    0.835294   6.575264  0.098049    5.300140       0.984158
5336                (22726)               (22727)            0.068404            0.068404  0.057003    0.833333  12.182540  0.052324    5.589577       0.985315
5337                (22727)               (22726)            0.068404            0.068404  0.057003    0.833333  12.182540  0.052324    5.589577       0.985315
15928         (POST, 21086)               (21094)            0.117264            0.127036  0.096091    0.819444   6.450499  0.081194    4.834878       0.957221
31043         (POST, 22727)               (22726)            0.061889            0.068404  0.050489    0.815789  11.926065  0.046255    5.057236       0.976591
5359                (22727)               (22728)            0.068404            0.073290  0.055375    0.809524  11.045503  0.050361    4.865228       0.976244
64669  (POST, 22556, 22551)               (22554)            0.068404            0.157980  0.055375    0.809524   5.124202  0.044568    4.420603       0.863945
14592        (21094, 21086)               (21080)            0.115635            0.133550  0.091205    0.788732   5.905874  0.075762    4.101194       0.939292
5339                (22726)               (22728)            0.068404            0.073290  0.053746    0.785714  10.720635  0.048733    4.324647       0.973299
47337  (21094, POST, 21086)               (21080)            0.096091            0.133550  0.074919    0.779661   5.837950  0.062086    3.932348       0.916804
47338        (21080, 21086)         (POST, 21094)            0.096091            0.107492  0.074919    0.779661   7.253210  0.064590    4.050614       0.953780
47340        (21080, 21094)         (POST, 21086)            0.096091            0.117264  0.074919    0.779661   6.648776  0.063651    4.006264       0.939914
5091                (22630)               (22629)            0.096091            0.130293  0.073290    0.762712   5.853814  0.060770    3.665193       0.917317
15933               (21094)         (POST, 21086)            0.127036            0.117264  0.096091    0.756410   6.450499  0.081194    3.623864       0.967936
1451                (21094)               (21080)            0.127036            0.133550  0.096091    0.756410   5.663852  0.079126    3.557003       0.943271
30419         (POST, 22630)               (22629)            0.073290            0.130293  0.055375    0.755556   5.798889  0.045825    3.557892       0.893001
5358                (22728)               (22727)            0.073290            0.068404  0.055375    0.755556  11.045503  0.050361    3.811075       0.981392
15036         (P

# 5. Suggesting Products to Users at the Cart Stage

In [50]:
product_id = 22492

In [51]:
check_id(df, product_id)

['MINI PAINT SET VINTAGE ']


In [52]:
sorted_rules = rules.sort_values("lift", ascending=False)

In [53]:
recommendation_list = []

In [54]:
for i, product in enumerate(sorted_rules["antecedents"]):
    for j in list(product):
        if j == product_id:
            recommendation_list.append(list(sorted_rules.iloc[i]["consequents"])[0])

In [55]:
recommendation_list[0:3]

[21914, 21080, 21080]

In [56]:
def arl_recommender(rules_df, product_id, rec_count=1):
    sorted_rules = rules_df.sort_values("lift", ascending=False)
    recommendation_list = []
    for i, product in enumerate(sorted_rules["antecedents"]):
        for j in list(product):
            if j == product_id:
                recommendation_list.append(list(sorted_rules.iloc[i]["consequents"])[0])

    return recommendation_list[0:rec_count]

In [57]:
arl_recommender(rules, 22492, 1)

[21914]

In [58]:
arl_recommender(rules, 22492, 2)

[21914, 21080]

In [59]:
arl_recommender(rules, 22492, 3)

[21914, 21080, 21080]